Capstone Project - The Battle of Neighborhoods

Melbourne is the food capital of Australia. A dynamic city with a vibrant food scene, very competitive but also plenty of opportunity if one has the right location.

In this project I will use location data and a clustering technique to answer the question

'Where is the best location to open a licensed restaurant in Melbourne'?

Data has been reieved from https://www.corra.com.au/australian-postcode-location-data/


In [1]:
!conda install -c conda-forge folium=0.5.0 --yes
import numpy as np
import pandas as pd
import requests, csv, json 
import matplotlib.cm as cm
import matplotlib.colors as colors
import folium
from pandas.io.json import json_normalize
from geopy.geocoders import Nominatim
from sklearn.cluster import KMeans

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - folium=0.5.0


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    vincent-0.4.4              |             py_1          28 KB  conda-forge
    openssl-1.1.1g             |       h516909a_1         2.1 MB  conda-forge
    branca-0.4.1               |             py_0          26 KB  conda-forge
    folium-0.5.0               |             py_0          45 KB  conda-forge
    python_abi-3.6             |          1_cp36m           4 KB  conda-forge
    certifi-2020.6.20          |   py36h9f0ad1d_0         151 KB  conda-forge
    altair-4.1.0               |             py_1         614 KB  conda-forge
    ca-certificates-2020.6.20  |       hecda079_0         145 KB  conda-forge
    ------------------------------------------------------------
                       

In [2]:
# The code was removed by Watson Studio for sharing.

Neighborhood   Latitude   Longitude
0           MELBOURNE -38.365017  144.765920
1      EAST MELBOURNE -37.816640  144.987811
2      WEST MELBOURNE -37.806255  144.941123
3           MELBOURNE -37.837324  144.976335
4  WORLD TRADE CENTRE -37.822262  144.954856

In [3]:
df=df_data_0

In [4]:
df.head()

Neighborhood   Latitude   Longitude
0           MELBOURNE -38.365017  144.765920
1      EAST MELBOURNE -37.816640  144.987811
2      WEST MELBOURNE -37.806255  144.941123
3           MELBOURNE -37.837324  144.976335
4  WORLD TRADE CENTRE -37.822262  144.954856

Visualizing the geographic data

In [36]:
latitude = -38.365017
longitude = 144.765920

map_melbourne = folium.Map(location=[latitude, longitude], zoom_start=12)

# add markers to map
for lat, lng, label in zip(df['Latitude'], df['Longitude'], df['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_melbourne)  
    
map_melbourne

Explore the Foursquare's API

In [5]:
CLIENT_ID = 'DCL0RCI3KZW3IQPMB43UY2L1DW2FQXAFEYRU0SF0M313L330'
CLIENT_SECRET = 'JB3AJOFJJCLTARHSUKTT5EL31XYHWLP1PJHMM24DDBUZRIRV'
VERSION = '20200831' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: DCL0RCI3KZW3IQPMB43UY2L1DW2FQXAFEYRU0SF0M313L330
CLIENT_SECRET:JB3AJOFJJCLTARHSUKTT5EL31XYHWLP1PJHMM24DDBUZRIRV


In [6]:
LIMIT = 100
radius = 100

neighborhood_latitude = -38.365017
neighborhood_longitude = 144.765920

url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)

url

'https://api.foursquare.com/v2/venues/explore?&client_id=DCL0RCI3KZW3IQPMB43UY2L1DW2FQXAFEYRU0SF0M313L330&client_secret=JB3AJOFJJCLTARHSUKTT5EL31XYHWLP1PJHMM24DDBUZRIRV&v=20200831&ll=-38.365017,144.76592&radius=100&limit=100'

In [44]:
results = requests.get(url).json()['response']['groups'][0]['items']

Explore neighborhoods

In [8]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    venues_list=[]
    
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [10]:
melbourne_venues = getNearbyVenues(names=df['Neighborhood'],
                                   latitudes=df['Latitude'],
                                   longitudes=df['Longitude']
                                  )

MELBOURNE
EAST MELBOURNE
WEST MELBOURNE
MELBOURNE
WORLD TRADE CENTRE
SOUTHBANK
DOCKLANDS
UNIVERSITY OF MELBOURNE
FOOTSCRAY
SEDDON
SEDDON WEST
BROOKLYN
KINGSVILLE
KINGSVILLE WEST
MAIDSTONE
TOTTENHAM
WEST FOOTSCRAY
YARRAVILLE
YARRAVILLE WEST
NEWPORT
SOUTH KINGSVILLE
SPOTSWOOD
WILLIAMSTOWN
WILLIAMSTOWN NORTH
ALTONA
SEAHOLME
BRAYBROOK
BRAYBROOK NORTH
ROBINSON
ALBION
GLENGALA
SUNSHINE NORTH
SUNSHINE WEST
ALBANVALE
KEALBA
KINGS PARK
ST ALBANS
ARDEER
DEER PARK EAST
BURNSIDE
BURNSIDE HEIGHTS
CAIRNLEA
CAROLINE SPRINGS
DEER PARK
DEER PARK NORTH
RAVENHALL
MAMBOURIN
MOUNT COTTRELL
WYNDHAM VALE
ALTONA EAST
ALTONA GATE
ALTONA NORTH
LAVERTON NORTH
LAVERTON RAAF
ALTONA MEADOWS
LAVERTON
SEABROOK
HOPPERS CROSSING
TARNEIT
TRUGANINA
COCOROC
DERRIMUT
POINT COOK
QUANDONG
WERRIBEE
WERRIBEE SOUTH
FLEMINGTON
KENSINGTON
ASCOT VALE
HIGHPOINT CITY
MARIBYRNONG
TRAVANCORE
KEILOR EAST
AVONDALE HEIGHTS
KEILOR
KEILOR NORTH
DELAHEY
HILLSIDE
SYDENHAM
TAYLORS HILL
KEILOR DOWNS
KEILOR LODGE
TAYLORS LAKES
WATERGARDENS
MOON

Check the size of resulting dataframe.

In [27]:
print(melbourne_venues.shape)
melbourne_venues.head()

(8909, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0       MELBOURNE             -38.365017              144.765920   
1  EAST MELBOURNE             -37.816640              144.987811   
2  EAST MELBOURNE             -37.816640              144.987811   
3  EAST MELBOURNE             -37.816640              144.987811   
4  EAST MELBOURNE             -37.816640              144.987811   

                    Venue  Venue Latitude  Venue Longitude   Venue Category  
0          Riley Plumbing      -38.367948       144.766502     Home Service  
1            Hard Pressed      -37.816612       144.987549             Café  
2        The Tippler & Co      -37.816510       144.988240         Wine Bar  
3              Yarra Park      -37.819311       144.986637             Park  
4  Krua Thai 2 Restaurant      -37.817631       144.991231  Thai Restaurant

In [28]:
melbourne_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                               
ABBOTSFORD                             24                      24     24   
ABECKETT STREET                       100                     100    100   
ABERFELDIE                              4                       4      4   
AIREYS INLET                            5                       5      5   
AIRPORT WEST                           21                      21     21   
ALBANVALE                               3                       3      3   
ALBERT PARK                            26                      26     26   
ALBION                                  4                       4      4   
ALEXANDRA                               5                       5      5   
ALFREDTON                               5                       5      5   
ALLANS FLAT                             1                       1      1   
ALPHINGTON                              7                       7      7   
ALTONA                                 11                      11     11   
ALTONA EAST                             4                       4      4   
ALTONA GATE                             4                       4      4   
ALTONA MEADOWS                          9                       9      9   
ALTONA NORTH                            3                       3      3   
AMOR                                    1                       1      1   
ANDERSON                                2                       2      2   
ANGLESEA                               16                      16     16   
APOLLO BAY                              2                       2      2   
APPIN PARK                              3                       3      3   
APSLEY                                  1                       1      1   
ARARAT                                 10                      10     10   
ARDEER                                  6                       6      6   
ARMADALE                               12                      12     12   
ARMADALE NORTH                         19                      19     19   
ARMSTRONG                               1                       1      1   
ARTHURS SEAT                            6                       6      6   
ASCOT VALE                              6                       6      6   
...                                   ...                     ...    ...   
WOOD WOOD                               1                       1      1   
WOODEND                                 9                       9      9   
WOODSIDE BEACH                          2                       2      2   
WOODSTOCK                               7                       7      7   
WOOMELANG                               2                       2      2   
WOORI YALLOCK                           3                       3      3   
WORLD TRADE CENTRE                    154                     154    154   
WUNGHNU                                 1                       1      1   
WURRUK                                  1                       1      1   
WYCHEPROOF                              4                       4      4   
WYE RIVER                               5                       5      5   
WYNDHAM VALE                            6                       6      6   
YACKANDANDAH                            4                       4      4   
YALLAMBIE                               4                       4      4   
YALLOURN NORTH                          3                       3      3   
YARRA GLEN                              9                       9      9   
YARRA JUNCTION                          4                       4      4   
YARRAGON                                4                       4      4   
YARRAM                                  4                       4      4   
YARRAMBAT                               1                       1   

In [29]:
print('There are {} uniques categories.'.format(len(melbourne_venues['Venue Category'].unique())))

There are 385 uniques categories.


Pre-Processing

In [30]:
# one hot encoding
df_onehot = pd.get_dummies(melbourne_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
df_onehot['Neighborhood'] = melbourne_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [df_onehot.columns[-1]] + list(df_onehot.columns[:-1])
melbourne_onehot = df_onehot[fixed_columns]

df_onehot.head()

Accessories Store  Afghan Restaurant  African Restaurant  Airport  \
0                  0                  0                   0        0   
1                  0                  0                   0        0   
2                  0                  0                   0        0   
3                  0                  0                   0        0   
4                  0                  0                   0        0   

   Airport Service  American Restaurant  Antique Shop  Apres Ski Bar  \
0                0                    0             0              0   
1                0                    0             0              0   
2                0                    0             0              0   
3                0                    0             0              0   
4                0                    0             0              0   

   Aquarium  Arcade  ...  Whisky Bar  Wine Bar  Wine Shop  Winery  \
0         0       0  ...           0         0          0       0   
1         0       0  ...           0         0          0       0   
2         0       0  ...           0         1          0       0   
3         0       0  ...           0         0          0       0   
4         0       0  ...           0         0          0       0   

   Wings Joint  Women's Store  Xinjiang Restaurant  Yemeni Restaurant  \
0            0              0                    0                  0   
1            0              0                    0                  0   
2            0              0                    0                  0   
3            0              0                    0                  0   
4            0              0                    0                  0   

   Yoga Studio  Zoo Exhibit  
0            0            0  
1            0            0  
2            0            0  
3            0            0  
4            0            0  

[5 rows x 385 columns]

In [31]:
df_onehot.shape

(8909, 385)

In [32]:
df_grouped = df_onehot.groupby('Neighborhood').mean().reset_index()
df_grouped

Neighborhood  Accessories Store  Afghan Restaurant  \
0             ABBOTSFORD                0.0                0.0   
1        ABECKETT STREET                0.0                0.0   
2             ABERFELDIE                0.0                0.0   
3           AIREYS INLET                0.0                0.0   
4           AIRPORT WEST                0.0                0.0   
5              ALBANVALE                0.0                0.0   
6            ALBERT PARK                0.0                0.0   
7                 ALBION                0.0                0.0   
8              ALEXANDRA                0.0                0.0   
9              ALFREDTON                0.0                0.0   
10           ALLANS FLAT                0.0                0.0   
11            ALPHINGTON                0.0                0.0   
12                ALTONA                0.0                0.0   
13           ALTONA EAST                0.0                0.0   
14           ALTONA GATE                0.0                0.0   
15        ALTONA MEADOWS                0.0                0.0   
16          ALTONA NORTH                0.0                0.0   
17                  AMOR                0.0                0.0   
18              ANDERSON                0.0                0.0   
19              ANGLESEA                0.0                0.0   
20            APOLLO BAY                0.0                0.0   
21            APPIN PARK                0.0                0.0   
22                APSLEY                0.0                0.0   
23                ARARAT                0.0                0.0   
24                ARDEER                0.0                0.0   
25              ARMADALE                0.0                0.0   
26        ARMADALE NORTH                0.0                0.0   
27             ARMSTRONG                0.0                0.0   
28          ARTHURS SEAT                0.0                0.0   
29            ASCOT VALE                0.0                0.0   
...                  ...                ...                ...   
1076           WOOD WOOD                0.0                0.0   
1077             WOODEND                0.0                0.0   
1078      WOODSIDE BEACH                0.0                0.0   
1079           WOODSTOCK                0.0                0.0   
1080           WOOMELANG                0.0                0.0   
1081       WOORI YALLOCK                0.0                0.0   
1082  WORLD TRADE CENTRE                0.0                0.0   
1083             WUNGHNU                0.0                0.0   
1084              WURRUK                0.0                0.0   
1085          WYCHEPROOF                0.0                0.0   
1086           WYE RIVER                0.0                0.0   
1087        WYNDHAM VALE                0.0                0.0   
1088        YACKANDANDAH                0.0                0.0   
1089           YALLAMBIE                0.0                0.0   
1090      YALLOURN NORTH                0.0                0.0   
1091          YARRA GLEN                0.0                0.0   
1092      YARRA JUNCTION                0.0                0.0   
1093            YARRAGON                0.0                0.0   
1094              YARRAM                0.0                0.0   
1095           YARRAMBAT                0.0                0.0   
1096          YARRAVILLE                0.0                0.0   
1097     YARRAVILLE WEST                0.0                0.0   
1098          YARRAWONGA                0.0                0.0   
1099            YARRUNGA                0.0                0.0   
1100                 YEA                0.0                0.0   
1101           YELLINGBO                0.0                0.0   
1102              YERING                0.0                0.0   
1103              YINNAR                0.0                0.0   
1104             YUULONG                0.0         

Check the size of grouped dataframe.

In [33]:
df_grouped.shape

(1106, 385)

The size of grouped dataframe is different from the neighborhood dataframe. Let's find out it.

In [ ]:
missing_neighborhood = [i for i in df_hk['Neighborhood'].unique() if i not in df_grouped['Neighborhood'].unique()]

missing_neighborhood

'Stonecutters Island' is missing in grouped dataframe. After some research, I find out that Stonecutters Island is a military port, so I decide to exclude it from the dataset.

In [ ]:
df_hk = df_hk[df_hk['Neighborhood'] != 'Stonecutters Island']

Print each neighborhood along with the top 5 most common venues.

In [34]:
num_top_venues = 5

for hood in df_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = df_grouped[df_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----ABBOTSFORD----
              venue  freq
0              Café  0.17
1               Pub  0.12
2  Football Stadium  0.04
3  Greek Restaurant  0.04
4       Coffee Shop  0.04


----ABECKETT STREET----
                   venue  freq
0                   Café  0.11
1            Coffee Shop  0.09
2      Korean Restaurant  0.08
3  Korean BBQ Restaurant  0.03
4             Donut Shop  0.03


----ABERFELDIE----
               venue  freq
0       Tennis Court  0.25
1        Sports Club  0.25
2      Grocery Store  0.25
3  Food & Drink Shop  0.25
4        Opera House  0.00


----AIREYS INLET----
               venue  freq
0               Café   0.4
1                Pub   0.2
2      Grocery Store   0.2
3   Greek Restaurant   0.2
4  Accessories Store   0.0


----AIRPORT WEST----
                  venue  freq
0  Fast Food Restaurant  0.10
1           Supermarket  0.10
2             Juice Bar  0.05
3     Electronics Store  0.05
4     Mobile Phone Shop  0.05


----ALBANVALE----
                    ve

In [35]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Create the new dataframe and display the top 10 venues for each neighborhood.

In [19]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = df_grouped['Neighborhood']

for ind in np.arange(df_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(df_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0       ABBOTSFORD                  Café                   Pub   
1  ABECKETT STREET                  Café           Coffee Shop   
2       ABERFELDIE           Sports Club          Tennis Court   
3     AIREYS INLET                  Café                   Pub   
4     AIRPORT WEST  Fast Food Restaurant           Supermarket   

           3rd Most Common Venue 4th Most Common Venue  5th Most Common Venue  \
0  Vegetarian / Vegan Restaurant           Pizza Place            Coffee Shop   
1              Korean Restaurant   Japanese Restaurant  Korean BBQ Restaurant   
2                  Grocery Store     Food & Drink Shop            Fabric Shop   
3                  Grocery Store      Greek Restaurant            Zoo Exhibit   
4             Light Rail Station      Video Game Store          Grocery Store   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0    Rock Climbing Spot              Dive Bar        Sandwich Place   
1            Donut Shop      Malay Restaurant         Shopping Mall   
2    Falafel Restaurant                  Farm        Farmers Market   
3     Fish & Chips Shop           Fabric Shop    Falafel Restaurant   
4                   Gym     Electronics Store                Bakery   

   9th Most Common Venue 10th Most Common Venue  
0                   Park         Farmers Market  
1  Indonesian Restaurant     Chinese Restaurant  
2   Fast Food Restaurant                  Field  
3                   Farm         Farmers Market  
4         Sandwich Place                   Café

Find out venues including bus or metro station.

In [20]:
df_station = melbourne_venues[melbourne_venues['Venue Category'].str.contains('Station$') |
                       melbourne_venues['Venue Category'].str.contains('^Bus')]
df_station.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
16  EAST MELBOURNE             -37.816640              144.987811   
24  EAST MELBOURNE             -37.816640              144.987811   
28  WEST MELBOURNE             -37.806255              144.941123   
32  WEST MELBOURNE             -37.806255              144.941123   
34  WEST MELBOURNE             -37.806255              144.941123   

                           Venue  Venue Latitude  Venue Longitude  \
16              Jolimont Station      -37.816466       144.984213   
24        Tram Stop 11 (48 & 75)      -37.816064       144.982618   
28                Platform 2 & 3      -37.807179       144.942048   
32  Melbourne Yard Wash Facility      -37.804620       144.938080   
34       North Melbourne Station      -37.807043       144.942042   

        Venue Category  
16       Train Station  
24  Light Rail Station  
28       Train Station  
32       Train Station  
34       Train Station

Insert a new column to represents if there is a station nearby.

In [21]:
cols = df_station['Neighborhood'].unique()
indice = neighborhoods_venues_sorted[neighborhoods_venues_sorted['Neighborhood'].isin(cols)].index.values

neighborhoods_venues_sorted['Station'] = 'No'
neighborhoods_venues_sorted.loc[indice, 'Station'] = 'Yes'

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0       ABBOTSFORD                  Café                   Pub   
1  ABECKETT STREET                  Café           Coffee Shop   
2       ABERFELDIE           Sports Club          Tennis Court   
3     AIREYS INLET                  Café                   Pub   
4     AIRPORT WEST  Fast Food Restaurant           Supermarket   

           3rd Most Common Venue 4th Most Common Venue  5th Most Common Venue  \
0  Vegetarian / Vegan Restaurant           Pizza Place            Coffee Shop   
1              Korean Restaurant   Japanese Restaurant  Korean BBQ Restaurant   
2                  Grocery Store     Food & Drink Shop            Fabric Shop   
3                  Grocery Store      Greek Restaurant            Zoo Exhibit   
4             Light Rail Station      Video Game Store          Grocery Store   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0    Rock Climbing Spot              Dive Bar        Sandwich Place   
1            Donut Shop      Malay Restaurant         Shopping Mall   
2    Falafel Restaurant                  Farm        Farmers Market   
3     Fish & Chips Shop           Fabric Shop    Falafel Restaurant   
4                   Gym     Electronics Store                Bakery   

   9th Most Common Venue 10th Most Common Venue Station  
0                   Park         Farmers Market     Yes  
1  Indonesian Restaurant     Chinese Restaurant      No  
2   Fast Food Restaurant                  Field      No  
3                   Farm         Farmers Market      No  
4         Sandwich Place                   Café     Yes

Clustering

Run k-means to cluster the neighborhood into 5 clusters.

In [22]:
# set number of clusters
kclusters = 5

melbourne_grouped_clustering = df_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(melbourne_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 0, 0, 2, 0, 0, 2, 0, 0, 0], dtype=int32)

Create a new dataframe that includes the cluster for each neighborhood.

In [45]:
df_grouped.head()

Neighborhood  Accessories Store  Afghan Restaurant  African Restaurant  \
0       ABBOTSFORD                0.0                0.0                 0.0   
1  ABECKETT STREET                0.0                0.0                 0.0   
2       ABERFELDIE                0.0                0.0                 0.0   
3     AIREYS INLET                0.0                0.0                 0.0   
4     AIRPORT WEST                0.0                0.0                 0.0   

   Airport  Airport Service  American Restaurant  Antique Shop  Aquarium  \
0      0.0              0.0                  0.0          0.00       0.0   
1      0.0              0.0                  0.0          0.01       0.0   
2      0.0              0.0                  0.0          0.00       0.0   
3      0.0              0.0                  0.0          0.00       0.0   
4      0.0              0.0                  0.0          0.00       0.0   

   Arcade  ...  Whisky Bar  Wine Bar  Wine Shop  Winery  Wings Joint  \
0     0.0  ...         0.0      0.00        0.0     0.0          0.0   
1     0.0  ...         0.0      0.01        0.0     0.0          0.0   
2     0.0  ...         0.0      0.00        0.0     0.0          0.0   
3     0.0  ...         0.0      0.00        0.0     0.0          0.0   
4     0.0  ...         0.0      0.00        0.0     0.0          0.0   

   Women's Store  Xinjiang Restaurant  Yemeni Restaurant  Yoga Studio  \
0            0.0                  0.0                0.0          0.0   
1            0.0                  0.0                0.0          0.0   
2            0.0                  0.0                0.0          0.0   
3            0.0                  0.0                0.0          0.0   
4            0.0                  0.0                0.0          0.0   

   Zoo Exhibit  
0          0.0  
1          0.0  
2          0.0  
3          0.0  
4          0.0  

[5 rows x 388 columns]

In [37]:
melbourne_grouped_clustering.head()

Accessories Store  Afghan Restaurant  African Restaurant  Airport  \
0                0.0                0.0                 0.0      0.0   
1                0.0                0.0                 0.0      0.0   
2                0.0                0.0                 0.0      0.0   
3                0.0                0.0                 0.0      0.0   
4                0.0                0.0                 0.0      0.0   

   Airport Service  American Restaurant  Antique Shop  Aquarium  Arcade  \
0              0.0                  0.0          0.00       0.0     0.0   
1              0.0                  0.0          0.01       0.0     0.0   
2              0.0                  0.0          0.00       0.0     0.0   
3              0.0                  0.0          0.00       0.0     0.0   
4              0.0                  0.0          0.00       0.0     0.0   

   Argentinian Restaurant  ...  Whisky Bar  Wine Bar  Wine Shop  Winery  \
0                    0.00  ...         0.0      0.00        0.0     0.0   
1                    0.01  ...         0.0      0.01        0.0     0.0   
2                    0.00  ...         0.0      0.00        0.0     0.0   
3                    0.00  ...         0.0      0.00        0.0     0.0   
4                    0.00  ...         0.0      0.00        0.0     0.0   

   Wings Joint  Women's Store  Xinjiang Restaurant  Yemeni Restaurant  \
0          0.0            0.0                  0.0                0.0   
1          0.0            0.0                  0.0                0.0   
2          0.0            0.0                  0.0                0.0   
3          0.0            0.0                  0.0                0.0   
4          0.0            0.0                  0.0                0.0   

   Yoga Studio  Zoo Exhibit  
0          0.0          0.0  
1          0.0          0.0  
2          0.0          0.0  
3          0.0          0.0  
4          0.0          0.0  

[5 rows x 387 columns]

In [23]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

melbourne_merged = df

# merge hk_grouped with hk_data to add latitude/longitude for each neighborhood
melbourne_merged = melbourne_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on=('Neighborhood'))

melbourne_merged.head() # check the last columns!

Neighborhood   Latitude   Longitude  Cluster Labels  \
0           MELBOURNE -38.365017  144.765920             0.0   
1      EAST MELBOURNE -37.816640  144.987811             0.0   
2      WEST MELBOURNE -37.806255  144.941123             0.0   
3           MELBOURNE -37.837324  144.976335             0.0   
4  WORLD TRADE CENTRE -37.822262  144.954856             0.0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0          Home Service                  Café    Light Rail Station   
1                  Café       Thai Restaurant     Indian Restaurant   
2         Train Station                  Café              Platform   
3          Home Service                  Café    Light Rail Station   
4                  Café                   Bar                 Hotel   

   4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0  Australian Restaurant                 Hotel        Sandwich Place   
1                 Museum    Light Rail Station      Sushi Restaurant   
2                    Bar              Bus Stop               Theater   
3  Australian Restaurant                 Hotel        Sandwich Place   
4    Japanese Restaurant           Coffee Shop                   Gym   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0            Steakhouse      Asian Restaurant           Pizza Place   
1                   Gym                  Park            Steakhouse   
2           Fabric Shop    Falafel Restaurant                  Farm   
3            Steakhouse      Asian Restaurant           Pizza Place   
4     French Restaurant    Italian Restaurant   Fried Chicken Joint   

  10th Most Common Venue Station  
0  Vietnamese Restaurant     Yes  
1         Hardware Store     Yes  
2         Farmers Market     Yes  
3  Vietnamese Restaurant     Yes  
4           Cocktail Bar      No

Visualize the result¶

In [ ]:
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

markers_colors = []
for lat, lon, poi, cluster in zip(melbourne_merged['Latitude'], melbourne_merged['Longitude'], melbourne_merged['Neighborhood'], melbourne_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

Cluster 1

In [39]:
melbourne_merged.loc[melbourne_merged['Cluster Labels'] == 0, melbourne_merged.columns[[1] + list(range(5, melbourne_merged.shape[1]))]]

Latitude          2nd Most Common Venue      3rd Most Common Venue  \
0    -38.365017                           Café         Light Rail Station   
1    -37.816640                Thai Restaurant          Indian Restaurant   
2    -37.806255                           Café                   Platform   
3    -37.837324                           Café         Light Rail Station   
4    -37.822262                            Bar                      Hotel   
5    -37.823258                            Bar              Grocery Store   
6    -37.814719                     Restaurant                Coffee Shop   
7    -37.796152                    Coffee Shop                        Pub   
8    -37.799770                           Café           Asian Restaurant   
10   -37.795059                            Gym              Grocery Store   
12   -37.812635                  Shopping Mall                 Skate Park   
13   -37.795059                            Gym              Grocery Store   
14   -37.782096      Latin American Restaurant                       Café   
15   -37.799065                  Train Station               Cupcake Shop   
16   -37.797701                           Park              Grocery Store   
17   -37.816178                    Pizza Place              Grocery Store   
18   -37.818019                     Kids Store               Soccer Field   
20   -37.833627                    Pizza Place                       Café   
21   -37.829670                           Café                Gas Station   
23   -37.857681              Convenience Store                        Pub   
24   -37.869275                   Burger Joint          Fish & Chips Shop   
25   -37.867992                  Train Station              Boat or Ferry   
26   -37.779309            Sporting Goods Shop              Grocery Store   
27   -37.845360                     Skate Park             Baseball Field   
29   -37.775954                    Music Store              Train Station   
32   -37.799830                  Jewelry Store              Grocery Store   
33   -37.745934         Furniture / Home Store            Laundry Service   
34   -37.742331                    Coffee Shop         Seafood Restaurant   
36   -37.745063                   Noodle House           Asian Restaurant   
37   -37.782920                            Pub           Football Stadium   
...         ...                            ...                        ...   
3132 -38.365017                           Café         Light Rail Station   
3133 -38.365017                           Café         Light Rail Station   
3134 -38.365017                           Café         Light Rail Station   
3135 -38.365017                           Café         Light Rail Station   
3136 -38.365017                           Café         Light Rail Station   
3137 -38.365017                           Café         Light Rail Station   
3138 -38.365017                           Café         Light Rail Station   
3139 -38.365017                           Café         Light Rail Station   
3140 -38.365017                           Café         Light Rail Station   
3141 -38.365017                           Café         Light Rail Station   
3142 -38.365017                           Café         Light Rail Station   
3143 -38.365017                           Café         Light Rail Station   
3144 -38.365017                           Café         Light Rail Station   
3145 -38.365017                           Café         Light Rail Station   
3146 -38.365017                           Café         Light Rail Station   
3147 -38.365017                           Café         Light Rail Station   
3148 -38.365017                           Café         Light Rail Station   
3149 -38.365017                           Café         Light Rail Station   
3150 -38.365017                           Café         Light Rail Station   
3151 -37.905996                       Bus Stop         Falafel Restaurant   
315

Cluster 2

In [40]:
melbourne_merged.loc[melbourne_merged['Cluster Labels'] == 1, melbourne_merged.columns[[1] + list(range(5, melbourne_merged.shape[1]))]]

Latitude 2nd Most Common Venue 3rd Most Common Venue  \
78   -37.700040          Tennis Court      Basketball Court   
109  -37.700648           Zoo Exhibit      Iraqi Restaurant   
180  -37.744219                  Park    Country Dance Club   
184  -37.739262          Tennis Court         Event Service   
193  -37.690585     Convenience Store           Zoo Exhibit   
197  -37.730758  Fast Food Restaurant           Zoo Exhibit   
217  -37.796947           Zoo Exhibit      Iraqi Restaurant   
275  -37.805715                   Bar           Zoo Exhibit   
279  -37.787064          Tennis Court              Pharmacy   
295  -37.780668           Pizza Place         Event Service   
707  -38.377660                  Park         Event Service   
770  -37.671854           Zoo Exhibit      Iraqi Restaurant   
883  -37.947695        Scenic Lookout           Zoo Exhibit   
964  -37.604862           Zoo Exhibit      Iraqi Restaurant   
1169 -37.192318           Zoo Exhibit      Iraqi Restaurant   
1255 -37.783465           Zoo Exhibit      Iraqi Restaurant   
1351 -37.081139                   Bar           Zoo Exhibit   
1790 -36.708908           Zoo Exhibit      Iraqi Restaurant   
2006 -36.401942        Sandwich Place           Zoo Exhibit   
2009 -36.402124        Sandwich Place           Zoo Exhibit   
2219 -36.098410                  Park           Frame Store   
2267 -36.536849             Hotel Bar           Zoo Exhibit   
2428 -37.493854           Zoo Exhibit      Iraqi Restaurant   
2455 -37.601480           Zoo Exhibit      Iraqi Restaurant   
2489 -37.825378           Zoo Exhibit      Iraqi Restaurant   
2499 -37.774889                  Park  Ethiopian Restaurant   
2648 -38.148870          Tennis Court         Event Service   
2733 -38.378924            Skate Park           Zoo Exhibit   
3051 -38.053275            Print Shop  Fast Food Restaurant   

     4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
78            Food Service           Zoo Exhibit           Fabric Shop   
109            Event Space           Fabric Shop    Falafel Restaurant   
180            Event Space           Fabric Shop    Falafel Restaurant   
184            Event Space           Fabric Shop    Falafel Restaurant   
193            Fish Market           Fabric Shop    Falafel Restaurant   
197       Iraqi Restaurant           Event Space           Fabric Shop   
217            Event Space           Fabric Shop    Falafel Restaurant   
275      French Restaurant           Fabric Shop    Falafel Restaurant   
279          Event Service           Event Space           Fabric Shop   
295            Event Space           Fabric Shop    Falafel Restaurant   
707            Event Space           Fabric Shop    Falafel Restaurant   
770            Event Space           Fabric Shop    Falafel Restaurant   
883   Ethiopian Restaurant           Event Space           Fabric Shop   
964            Event Space           Fabric Shop    Falafel Restaurant   
1169           Event Space           Fabric Shop    Falafel Restaurant   
1255           Event Space           Fabric Shop    Falafel Restaurant   
1351     French Restaurant           Fabric Shop    Falafel Restaurant   
1790           Event Space           Fabric Shop    Falafel Restaurant   
2006  Ethiopian Restaurant           Event Space           Fabric Shop   
2009  Ethiopian Restaurant           Event Space           Fabric Shop   
2219         Event Service           Event Space           Fabric Shop   
2267     Fish & Chips Shop           Event Space           Fabric Shop   
2428           Event Space           Fabric Shop    Falafel Restaurant   
2455           Event Space           Fabric Shop    Falafel Restaurant   
2489           Event Space           Fabric Shop    Falafel Restaurant   
2499           Event Space           Fabric Shop    Falafel Restaurant   
2648           Event Space           Fabric Shop    Falafel Restaurant   
2733           Frame Store           Event S

Cluster 3

In [41]:
melbourne_merged.loc[melbourne_merged['Cluster Labels'] == 2, melbourne_merged.columns[[1] + list(range(5, melbourne_merged.shape[1]))]]

Latitude       2nd Most Common Venue  3rd Most Common Venue  \
9    -37.808769                      Bakery            Pizza Place   
11   -37.814624           Electronics Store             Food Truck   
19   -37.842477               Grocery Store         Cooking School   
22   -37.856902                        Park             Restaurant   
28   -37.834094          Chinese Restaurant           Gourmet Shop   
67   -37.794333                        Park    Fried Chicken Joint   
84   -37.765707                 Supermarket                    Bar   
86   -37.754973           Convenience Store            Sports Club   
116  -37.778987                 Pizza Place      Indian Restaurant   
126  -37.764910                        Park                    Pub   
152  -37.779039          Seafood Restaurant          Train Station   
153  -37.755040                         Bar     Italian Restaurant   
171  -37.772830                 Supermarket       Greek Restaurant   
183  -37.742893                      Bakery          Grocery Store   
196  -37.639769                 Zoo Exhibit     Country Dance Club   
198  -37.715294                         Pub          Train Station   
204  -37.692032                Home Service                   Café   
205  -37.670580                 Zoo Exhibit     Country Dance Club   
208  -37.640166               Train Station          Grocery Store   
212  -37.797982                         Gym     Italian Restaurant   
216  -37.792835                    Pharmacy        Thai Restaurant   
224  -37.757762                 Supermarket  Portuguese Restaurant   
227  -37.736915                 Candy Store                Dog Run   
233  -37.829719                 Coffee Shop        Harbor / Marina   
242  -37.832121          Light Rail Station       Asian Restaurant   
245  -37.825705                        Park      Convenience Store   
246  -37.825705                        Park      Convenience Store   
248  -37.843985         Japanese Restaurant      Electronics Store   
250  -37.844825                        Park          Grocery Store   
252  -37.835047           Fish & Chips Shop                   Park   
...         ...                         ...                    ...   
2449 -37.816839                 Bus Station                   Park   
2462 -37.654137                      Bakery            Supermarket   
2468 -37.510449  Tourist Information Center    Sporting Goods Shop   
2473 -37.929232                         Bar                   Café   
2484 -37.887353                 Zoo Exhibit     Country Dance Club   
2498 -37.753701          Italian Restaurant         Ice Cream Shop   
2500 -37.910545            Asian Restaurant                    Bar   
2508 -38.030467                        Park                    Pub   
2543 -38.026908                        Café            Zoo Exhibit   
2568 -38.203886               Train Station            Zoo Exhibit   
2707 -37.843462                        Café          Event Service   
2710 -37.966701                      Bakery            Supermarket   
2729 -37.800359                        Café            Zoo Exhibit   
2822 -37.795334                         Pub      Convenience Store   
2826 -37.707336                 Supermarket                 Bakery   
2840 -37.564236                        Lake                 Bakery   
2859 -37.374717                 Zoo Exhibit     Country Dance Club   
2877 -37.098832                       Motel             Restaurant   
2902 -38.392646                     Brewery                   Café   
2920 -38.499790                        Farm                   Café   
2929 -38.473815                      Bakery   Fast Food Restaurant   
2931 -38.187263                      Bakery          Grocery Store   
2942 -38.464988                 Zoo Exhibit     Country Dance Club   
2950 -38.344297              Breakfast Spot                  Motel   
2952 -37.970297                        Café           Dessert Shop   
2986 -38.531629  

Cluster 4

In [42]:
melbourne_merged.loc[melbourne_merged['Cluster Labels'] == 3, melbourne_merged.columns[[1] + list(range(5, melbourne_merged.shape[1]))]]

Latitude 2nd Most Common Venue   3rd Most Common Venue  \
31   -37.768904          Skating Rink             Gas Station   
35   -37.734277                   Pub              Restaurant   
74   -37.718965                   Pub                    Café   
87   -37.753802           Sports Club                     Pub   
142  -37.529372                  Café          Sandwich Place   
460  -38.099498                   Pub           Train Station   
481  -38.180291            Sports Bar                     Pub   
496  -38.142320                   Pub              Restaurant   
530  -38.344147                   Pub             Zoo Exhibit   
612  -38.193925    Italian Restaurant             Zoo Exhibit   
687  -38.081236  Fast Food Restaurant                  Bakery   
713  -38.292155                   Pub                   Diner   
743  -37.875220                   Pub              Campground   
746  -38.046590                   Pub             Gas Station   
864  -38.100967                   Pub              Restaurant   
881  -38.046528                   Pub           Train Station   
963  -37.712432     Food & Drink Shop             Golf Course   
1032 -37.555477                   Pub             Zoo Exhibit   
1049 -37.686374                   Pub               Gift Shop   
1205 -35.727235          Burger Joint                    Lake   
1258 -36.741816                   Pub       Indian Restaurant   
1289 -37.637155           Zoo Exhibit             Fish Market   
1336 -37.021382                  Café             Gas Station   
1370 -37.472283                   Pub                    Café   
1537 -35.980771                   Pub        Sculpture Garden   
1560 -35.382896           Zoo Exhibit             Fish Market   
1570 -34.308353                  Park                     Pub   
1572 -34.387210           Zoo Exhibit             Fish Market   
1585 -34.167929                   Pub           Grocery Store   
1614 -36.412547                   Pub                   Diner   
...         ...                   ...                     ...   
1990 -36.249386                   Pub             Art Gallery   
2054 -35.955363                   Pub           Grocery Store   
2055 -35.916758                   Pub           Grocery Store   
2060 -36.327503                  Café             Zoo Exhibit   
2070 -37.203001         Grocery Store                    Café   
2075 -37.236985           Zoo Exhibit             Fish Market   
2156 -36.353243  Fast Food Restaurant                   Track   
2158 -36.353243  Fast Food Restaurant                   Track   
2208 -36.053735         Grocery Store                Wine Bar   
2248 -36.141317                   Pub            Carpet Store   
2263 -36.533461                   Pub             Zoo Exhibit   
2280 -36.048986           Zoo Exhibit             Fish Market   
2285 -35.963832                   Pub             Zoo Exhibit   
2351 -36.340096           Zoo Exhibit             Fish Market   
2401 -36.892030              Ski Area          Ice Cream Shop   
2408 -36.404888        Farmers Market               Gastropub   
2412 -36.312970                Bakery            Antique Shop   
2436 -37.641394                   Pub             Zoo Exhibit   
2490 -37.863663           Zoo Exhibit             Fish Market   
2521 -38.080980                   Pub             Zoo Exhibit   
2582 -37.975325     Convenience Store              Campground   
2602 -38.072343                  Lake             Zoo Exhibit   
2686 -38.124641                   Pub           Grocery Store   
2788 -37.497243                   Pub             Zoo Exhibit   
2889 -37.859049                 Beach                    Lake   
3028 -38.665564                   Pub  Thrift / Vintage Store   
3049 -38.562402                   Pub             Supermarket   
3101 -38.563459  Fast Food Restaurant             Zoo Exhibit   
3109 -38.549173                   Pub               Surf Spot   
3112 -38.564322  Fast Food Restaurant     

Cluster 5

In [43]:
melbourne_merged.loc[melbourne_merged['Cluster Labels'] == 4, melbourne_merged.columns[[1] + list(range(5, melbourne_merged.shape[1]))]]

Latitude 2nd Most Common Venue 3rd Most Common Venue  \
526  -38.293801           Zoo Exhibit    Country Dance Club   
539  -38.748434            Campground           Zoo Exhibit   
657  -38.346708           Zoo Exhibit    Country Dance Club   
888  -37.962809                  Lake           Zoo Exhibit   
986  -37.484940           Zoo Exhibit    Country Dance Club   
1326 -37.286853           Zoo Exhibit    Country Dance Club   
1359 -37.153711           Zoo Exhibit    Country Dance Club   
1736 -36.803325           Zoo Exhibit    Country Dance Club   
2096 -36.802505            Campground           Zoo Exhibit   
2171 -36.652345           Zoo Exhibit    Country Dance Club   
2251 -36.220609           Zoo Exhibit    Country Dance Club   
2268 -36.177054           Zoo Exhibit    Country Dance Club   
2297 -37.321513            Food Stand           Zoo Exhibit   
2399 -36.772777           Zoo Exhibit    Country Dance Club   
2427 -37.450676           Zoo Exhibit    Country Dance Club   
2805 -37.733238        Shop & Service                 Motel   
2847 -37.475736            Campground     French Restaurant   
2994 -38.889520           Zoo Exhibit    Country Dance Club   

     4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
526            Fabric Shop    Falafel Restaurant                  Farm   
539            Fish Market           Fabric Shop    Falafel Restaurant   
657            Fabric Shop    Falafel Restaurant                  Farm   
888          Event Service           Fabric Shop    Falafel Restaurant   
986            Fabric Shop    Falafel Restaurant                  Farm   
1326           Fabric Shop    Falafel Restaurant                  Farm   
1359           Fabric Shop    Falafel Restaurant                  Farm   
1736           Fabric Shop    Falafel Restaurant                  Farm   
2096           Fish Market           Fabric Shop    Falafel Restaurant   
2171           Fabric Shop    Falafel Restaurant                  Farm   
2251           Fabric Shop    Falafel Restaurant                  Farm   
2268           Fabric Shop    Falafel Restaurant                  Farm   
2297           Fish Market           Fabric Shop    Falafel Restaurant   
2399           Fabric Shop    Falafel Restaurant                  Farm   
2427           Fabric Shop    Falafel Restaurant                  Farm   
2805           Zoo Exhibit           Fish Market           Fabric Shop   
2847           Fabric Shop    Falafel Restaurant                  Farm   
2994           Fabric Shop    Falafel Restaurant                  Farm   

     7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
526         Farmers Market  Fast Food Restaurant                 Field   
539                   Farm        Farmers Market  Fast Food Restaurant   
657         Farmers Market  Fast Food Restaurant                 Field   
888                   Farm        Farmers Market  Fast Food Restaurant   
986         Farmers Market  Fast Food Restaurant                 Field   
1326        Farmers Market  Fast Food Restaurant                 Field   
1359        Farmers Market  Fast Food Restaurant                 Field   
1736        Farmers Market  Fast Food Restaurant                 Field   
2096                  Farm        Farmers Market  Fast Food Restaurant   
2171        Farmers Market  Fast Food Restaurant                 Field   
2251        Farmers Market  Fast Food Restaurant                 Field   
2268        Farmers Market  Fast Food Restaurant                 Field   
2297                  Farm        Farmers Market  Fast Food Restaurant   
2399        Farmers Market  Fast Food Restaurant                 Field   
2427        Farmers Market  Fast Food Restaurant                 Field   
2805    Falafel Restaurant                  Farm        Farmers Market   
2847        Farmers Market  Fast Food Restaurant                 Field   
2994        Farmers Market  Fast Food Restaurant                 Field

In conclusion, the best location to open a restaurant in Melbourne will be in Cluster 4. This cluster has the most variety of restaurant and will be optimal for a licensed premises.

Detailed conclusion will be including in the report.